## Feature Extraction

**Packages**

In [2]:
import os
import pandas as pd
import numpy as np

import torch
import torchvision.models as tmodels
from torch.autograd import Variable
from torchvision import transforms

import cv2
from PIL import Image
import h5py
from tqdm import tqdm
from time import time

**Variables**

In [23]:
EXTRACT_FREQUENCY = 15
BATCH_SIZE = 16

args = {'use_cpu':True}

##### )) Paths

In [4]:

datasets_path='../data'
public_dataset_path=datasets_path+'/Public datasets'
tvsum_data = public_dataset_path+'/ydata-tvsum50-v1_1'
summe_data = public_dataset_path+'/SUMMe'
custom_data = datasets_path+'/Custom data'


features_path = 'extracted_features'
normalFt_path = features_path+'/normal'
hashbasedFt_path = features_path+'/hashbased'

##### )) GoogLeNet Model

In [6]:
googlenet = tmodels.googlenet(pretrained=True)
googlenet = torch.nn.Sequential(*list(googlenet.children())[:-2])
googlenet.eval()

Sequential(
  (0): BasicConv2d(
    (conv): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (1): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=True)
  (2): BasicConv2d(
    (conv): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (3): BasicConv2d(
    (conv): Conv2d(64, 192, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(192, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (4): MaxPool2d(kernel_size=3, stride=2, padding=0, dilation=1, ceil_mode=True)
  (5): Inception(
    (branch1): BasicConv2d(
      (conv): Conv2d(192, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
    )
    (bra

In [7]:
device = 'cuda' if torch.cuda.is_available() and not use_cpu else 'cpu'
googlenet = googlenet.to(device)

##### )) Frame preprocessing

In [8]:
  
def preprocess(frame):
    tr = transforms.Compose([
        transforms.Resize(224),
        # transforms.CenterCrop(224),
        transforms.ToTensor(),
        transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
    ])
    
    im = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB) # BGR to RGB
    im = Image.fromarray(im) # cv2 to PIL
    im = tr(im)
    fr = np.array(im)
    
    return fr


In [9]:
x=0

In [ ]:
x+15.6

### Extraction Modules

##### )) Hashed based features

In [16]:
def dhash(img):
    img=cv2.resize(img,(9,8),interpolation=cv2.INTER_CUBIC)
    # gray=cv2.cvtColor(img,cv2.COLOR_BGR2GRAY)
    gray=cv2.cvtColor(img,cv2.COLOR_RGB2GRAY)

    dhash_str = ''
    for i in range(8):
        for j in range(8):
            if gray[i, j] > gray[i, j + 1]:
                dhash_str = dhash_str + '1'
            else:
                dhash_str = dhash_str + '0'
    result = ''
    for i in range(0, len(dhash_str), 4):
        result += ''.join('%x' % int(dhash_str[i: i + 4], 2))
    # print(result)
    return result

def hamming(s1, s2):
    assert len(s1) == len(s2)
    return sum([ch1 != ch2 for ch1, ch2 in zip(s1, s2)])

In [17]:
def hash_gen_features(path, threshold):
    cap = cv2.VideoCapture(path)
    frames=[]
    video_features = []
    frame_count = cap.get(cv2.CAP_PROP_FRAME_COUNT)
    fps = cap.get(cv2.CAP_PROP_FPS)
    count = 0
    skip_count = 0
    
    nframes = frame_count//EXTRACT_FREQUENCY * EXTRACT_FREQUENCY
    
    with torch.no_grad():
        base = None
        hash1 = None
        while cap.isOpened():
            # Capture frame-by-frame
            ret, fr = cap.read()
            if ret is False:
                break
            count += 1
            
            frame = preprocess(fr)

            if count % EXTRACT_FREQUENCY == 0:
                hash2=dhash(fr)
                if hash1 is not None:
                    dist = hamming(hash1,hash2)
                if base is None or dist > threshold:
                    base = fr
                    hash1 = hash2
                    frames.append(frame)
                else:
                    skip_count += 1
                    frames.append(frame)
                    
                if (len(frames) == BATCH_SIZE) or (count == nframes and len(frames) > 0):
                    batch = np.array(frames)
                    if args['use_cpu']:
                        variable = Variable(torch.from_numpy(batch).float())
                        feature = googlenet(variable).detach().numpy()
                    else:
                        variable = Variable(torch.from_numpy(batch).float()).cuda()
                        feature = googlenet(variable).cpu().detach().numpy()
                        
                    video_features.extend(feature)
                    frames.clear()
                    

    cap.release()
    video_features = np.squeeze(np.array(video_features))
    return video_features, frame_count, fps

##### )) Normal features

In [20]:
def gen_features(path):
    cap = cv2.VideoCapture(path)
    count = 0
    frames = []
    video_features = []
    frame_count = cap.get(cv2.CAP_PROP_FRAME_COUNT)
    fps = cap.get(cv2.CAP_PROP_FPS)
    nframes = frame_count//EXTRACT_FREQUENCY * EXTRACT_FREQUENCY
    
    with torch.no_grad():
        
        while cap.isOpened():
            ret, fr = cap.read()
            if ret is False:
                break

            fr = preprocess(fr)
            
            count += 1
            if count % EXTRACT_FREQUENCY == 0:
                # frames.append(np.rollaxis(fr, 2))
                frames.append(fr)
                
                
            if (len(frames) == BATCH_SIZE) or (count == nframes and len(frames) > 0):
                batch = np.array(frames)
                # print(batch.shape)
                if args['use_cpu']:
                    variable = Variable(torch.from_numpy(batch).float())
                    feature = googlenet(variable).detach().numpy()
                else:
                    variable = Variable(torch.from_numpy(batch).float()).cuda()
                    feature = googlenet(variable).cpu().detach().numpy()
                video_features.extend(feature)
                frames.clear()
    
            
    cap.release()

    video_features = np.squeeze(np.array(video_features))
    return video_features, frame_count, fps

##### )) Feature extraction and storage

In [25]:
def extract_features(videos_path, h5output_path, method=None, names=None):
    h5_file = h5output_path
    # st = time()

    with h5py.File(h5_file, 'w') as f:
        files = os.listdir(videos_path)
        cnt = 0
        
        pbar = tqdm(total = len(files), position=0, leave=True)
        for file in files:
            cnt += 1
            path = videos_path + "/" + file
            
            if method == 'hashbased':
                video_features, fcnt, fps = hash_gen_features(path,4.0)
            else:
                video_features, fcnt, fps = gen_features(path)

            video_length = fcnt/fps
            
            if names:
                video_ = 'video_'+str(names.index(file.split(".")[0])+1)
            else:
                video_ = 'video_'+str(cnt)

            print(cnt,'.', video_, "no. of frames=", fcnt, "Output dimension=", video_features.shape)

            f.create_dataset(video_ + '/n_frames', data=int(fcnt))
            f.create_dataset(video_ + '/fps', data=int(fps))
            f.create_dataset(video_ + '/features', data=video_features)
            picks = np.arange(0, video_features.shape[0]) * EXTRACT_FREQUENCY
            # picks = np.arange(0, video_features.shape[0]) * int(fps//2)
            f.create_dataset(video_ + '/picks', data=picks)
            f.create_dataset(video_+'/duration', data=video_length)
            f.create_dataset(video_+'/video_name', data=str(file))
            pbar.update(1)


### TVSum feature extraction

##### )) TVSumm info

In [52]:
tvsum_info=pd.read_csv(tvsum_data+'/data/ydata-tvsum50-info.tsv',sep='\t')
tvsum_info

category     video_id                                              title  \
0        VT  AwmHb44_ouw  #1306 How to change tires for off road vehicle...   
1        VT  98MoyGZKHXc        How to use a tyre repair kit - Which? guide   
2        VT  J0nA4VgnoCo                                   #0001: FLAT TIRE   
3        VT  gzDbaEs1Rlg                 ŠKODA Tips How to Repair Your Tyre   
4        VT  XzYM3PfTM4w                     When to Replace Your Tires GMC   
5        VU  HT5vyqe0Xaw  The stuck truck of Mark, The rut that filled a...   
6        VU  sTEELN-vY30                             BBC - Train crash 2013   
7        VU  vdmoEJ5YbrQ  #453 girl gets van stuck in the back fourty [D...   
8        VU  xwqBXPGE9pQ      Smart Electric Vehicle Balances on Two Wheels   
9        VU  akI8YFjEmUw              Electric cars making earth more green   
10       GA  i3wAGJaaktw  Pet Joy Spa Grooming Services | Brentwood, CA ...   
11       GA  Bhxk-O1Y7Ho  Vlog #509 I'M A PUPPY DOG GROOMER! September 1...   
12       GA  0tmA_C6XwfM     Nail clipper Gloria Pets professional grooming   
13       GA  3eYKfiOEJNs                       Dog Grooming in Buenos Aires   
14       GA  xxdtq8mxegs      How to Clean Your Dog's Ears - Vetoquinol USA   
15       MS  WG0MBPpPC6I              Mexican Fried Chicken Sandwich Recipe   
16       MS  Hl-__g2gn_A      Reuben Sandwich with Corned Beef & Sauerkraut   
17       MS  Yi4Ij2NM7U4           Poor Man's Meals: Spicy Sausage Sandwich   
18       MS  37rzWOQsNIw  Saigon Sandwich - Vietnamese Sandwiches in San...   
19       MS  LRw_obCPUt0  GoogaMooga Sneak Peek Joseph Leonard's Fried C...   
20       PK  cjibtmSLxQ4  David Belle | Fondateur du parkour | Reportage...   
21       PK  b626MiF1ew4        Charlotte Parkour | Charlotte Video Project   
22       PK  XkqCExn6_Us  Singapore Parkour Free Running | JC Boy Late f...   
23       PK  GsAD1KT1xo8                               Parkour Camp Leipzig   
24       PK  PJrm840pAUI           Vivencias: Jam Parkour Viña del Mar 2012   
25       PR  91IHQYk1IQM  Chinese New Year Parade 2012 New York City Chi...   
26       PR  RBCABdttQmI        2013 Alumnae Parade & Laurel Chain Ceremony   
27       PR  z_6gVvQb2d0         LA Kings Stanley Cup South Bay Parade 2014   
28       PR  fWutDQy1nnY                                   Chinatown Parade   
29       PR  4wU_LUjG5Ic  Southend-on-Sea and Kortrijk Bike Friendly Cit...   
30       FM  VuWGsYPqAX8  Flash mob protest for Syria | Sydney, Australi...   
31       FM  JKpqYvAdIsw  ICC World Twenty20 Bangladesh 2014 Flash Mob -...   
32       FM  xmEERLqJ2kU  Bluffton Teachers Flash Mob Dance (A Staff tha...   
33       FM  byxOvuiIJV0  ICC World Twenty 20 Bangladesh 2014, Flash Mob...   
34       FM  _xMr-HKMfVA  CASACL - Flashmob in Copenhagen underground - ...   
35       BK  WxtbjNsCQ8A                                  Beekeeping101.mov   
36       BK  uGu_10sucQo                               A Year of Beekeeping   
37       BK  EE-bNr36nyA            Paper Wasp Removal | From the Ground Up   
38       BK  Se3oxnaPsz0  9/15/11 Killer Bees Kill 1000-lb Hog in Bisbee AZ   
39       BK  oDXZc0tZe04              Apis Mellifera in a Vertical Log Hive   
40       BT  qqR6AEXwxoQ  Motocross Tips & Tricks : How to Whip a Motocr...   
41       BT  EYqVtI9YWJA                  Smage Bros. Motorcycle Stunt Show   
42       BT  eQu1rNs0an0                             How to stop your Fixie   
43       BT  JgHubY5Vw3Y              How to lock your bike. The RIGHT way!   
44       BT  iVt07TCkFM0                        Pure Fix TV: How to Wheelie   
45       DS  E11zDS9XGzg         German Shepherd Dog Show (KCI) | DoHangout   
46       DS  NyBmCxDoHJU                               The Dog Show HD 720p   
47       DS  kLxoNp-UchI                         Oliver's Show - Dog's tale   
48       DS  jcoYJXDG9sw  TODAY- Obie the obese dog works toward weight ...   
49       DS  -esJrBWj2d8                           Wi

##### )) Videos

In [53]:
os.listdir(tvsum_data+'/video')

['-esJrBWj2d8.mp4',
 '0tmA_C6XwfM.mp4',
 '37rzWOQsNIw.mp4',
 '3eYKfiOEJNs.mp4',
 '4wU_LUjG5Ic.mp4',
 '91IHQYk1IQM.mp4',
 '98MoyGZKHXc.mp4',
 'akI8YFjEmUw.mp4',
 'AwmHb44_ouw.mp4',
 'b626MiF1ew4.mp4',
 'Bhxk-O1Y7Ho.mp4',
 'byxOvuiIJV0.mp4',
 'cjibtmSLxQ4.mp4',
 'E11zDS9XGzg.mp4',
 'EE-bNr36nyA.mp4',
 'eQu1rNs0an0.mp4',
 'EYqVtI9YWJA.mp4',
 'fWutDQy1nnY.mp4',
 'GsAD1KT1xo8.mp4',
 'gzDbaEs1Rlg.mp4',
 'Hl-__g2gn_A.mp4',
 'HT5vyqe0Xaw.mp4',
 'i3wAGJaaktw.mp4',
 'iVt07TCkFM0.mp4',
 'J0nA4VgnoCo.mp4',
 'jcoYJXDG9sw.mp4',
 'JgHubY5Vw3Y.mp4',
 'JKpqYvAdIsw.mp4',
 'kLxoNp-UchI.mp4',
 'LRw_obCPUt0.mp4',
 'NyBmCxDoHJU.mp4',
 'oDXZc0tZe04.mp4',
 'PJrm840pAUI.mp4',
 'qqR6AEXwxoQ.mp4',
 'RBCABdttQmI.mp4',
 'Se3oxnaPsz0.mp4',
 'sTEELN-vY30.mp4',
 'uGu_10sucQo.mp4',
 'vdmoEJ5YbrQ.mp4',
 'VuWGsYPqAX8.mp4',
 'WG0MBPpPC6I.mp4',
 'WxtbjNsCQ8A.mp4',
 'XkqCExn6_Us.mp4',
 'xmEERLqJ2kU.mp4',
 'xwqBXPGE9pQ.mp4',
 'xxdtq8mxegs.mp4',
 'XzYM3PfTM4w.mp4',
 'Yi4Ij2NM7U4.mp4',
 'z_6gVvQb2d0.mp4',
 '_xMr-HKMfVA.mp4']

##### )) Extraction

In [74]:
vnames = tvsum_info['video_id'].tolist()
extract_features(videos_path=tvsum_data+'/video', h5output_path=normalFt_path+'/TVSum05s.h5', names=vnames)

  2%|▏         | 1/50 [00:37<30:48, 37.73s/it]

1 . video_50 no. of frames= 6912.0 Output dimension= (460, 1024)


  4%|▍         | 2/50 [01:00<23:03, 28.83s/it]

2 . video_13 no. of frames= 3532.0 Output dimension= (282, 1024)


  6%|▌         | 3/50 [01:32<23:40, 30.22s/it]

...

48 . video_18 no. of frames= 9731.0 Output dimension= (810, 1024)


 98%|█████████▊| 49/50 [31:30<00:41, 41.15s/it]

49 . video_28 no. of frames= 8281.0 Output dimension= (552, 1024)


100%|██████████| 50/50 [31:53<00:00, 38.27s/it]

50 . video_35 no. of frames= 4463.0 Output dimension= (297, 1024)


## Custom Dataset

In [26]:
extract_features(videos_path='../data/Custom dataset', h5output_path=normalFt_path+'/customSet.h5')

 20%|██        | 1/5 [00:33<02:14, 33.67s/it]

1 . video_1 no. of frames= 3532.0 Output dimension= (235, 1024)


 40%|████      | 2/5 [01:06<01:38, 32.97s/it]

2 . video_2 no. of frames= 4853.0 Output dimension= (323, 1024)


 60%|██████    | 3/5 [40:41<36:45, 1102.64s/it]

3 . video_3 no. of frames= 146247.0 Output dimension= (9749, 1024)


 80%|████████  | 4/5 [44:10<12:29, 749.89s/it] 

4 . video_4 no. of frames= 13260.0 Output dimension= (884, 1024)


100%|██████████| 5/5 [46:22<00:00, 556.40s/it]

5 . video_5 no. of frames= 5320.0 Output dimension= (354, 1024)


### SUMMe feature extraction

##### )) SUMMe info

In [6]:
# summe_info=pd.read_csv(summe_data+'/summe_info.tsv',sep='\t')
# summe_info

video_id
0               Air_Force_One
1                Base jumping
2           Bearpark_climbing
3                   Bike Polo
4          Bus_in_Rock_Tunnel
5             car_over_camera
6            Car_railcrossing
7             Cockpit_Landing
8                     Cooking
9                Eiffel Tower
10  Excavators river crossing
11                Fire Domino
12                      Jumps
13     Kids_playing_in_leaves
14                 Notre_Dame
15                  Paintball
16                paluma_jump
17               playing_ball
18     Playing_on_water_slide
19           Saving dolphines
20                      Scuba
21         St Maarten Landing
22          Statue of Liberty
23       Uncut_Evening_Flight
24        Valparaiso_Downhill

##### )) Videos

In [7]:
# os.listdir(summe_data+'/videos')

['.htaccess',
 'Air_Force_One.mp4',
 'Base jumping.mp4',
 'Bearpark_climbing.mp4',
 'Bike Polo.mp4',
 'Bus_in_Rock_Tunnel.mp4',
 'car_over_camera.mp4',
 'Car_railcrossing.mp4',
 'Cockpit_Landing.mp4',
 'Cooking.mp4',
 'Eiffel Tower.mp4',
 'Excavators river crossing.mp4',
 'Fire Domino.mp4',
 'Jumps.mp4',
 'Kids_playing_in_leaves.mp4',
 'Notre_Dame.mp4',
 'Paintball.mp4',
 'paluma_jump.mp4',
 'playing_ball.mp4',
 'Playing_on_water_slide.mp4',
 'Saving dolphines.mp4',
 'Scuba.mp4',
 'St Maarten Landing.mp4',
 'Statue of Liberty.mp4',
 'Uncut_Evening_Flight.mp4',
 'Valparaiso_Downhill.mp4',
 'videos2frames.sh~']

##### )) Extraction

In [ ]:
# vnames = summe_info['video_id'].tolist()
# extract_features(videos_path=summe_data+'/videos', h5output_path=normalFt_path+'/SUMMe.h5')

  4%|▍         | 1/25 [01:54<45:40, 114.19s/it]

1 . video_1 no. of frames= 4494.0 Output dimension= (299, 1024)


  8%|▊         | 2/25 [02:49<30:23, 79.27s/it] 

2 . video_2 no. of frames= 4729.0 Output dimension= (315, 1024)


 12%|█▏        | 3/25 [03:40<24:20, 66.40s/it]

...

23 . video_23 no. of frames= 3863.0 Output dimension= (257, 1024)


 96%|█████████▌| 24/25 [23:26<01:08, 68.55s/it]

24 . video_24 no. of frames= 9672.0 Output dimension= (644, 1024)


100%|██████████| 25/25 [24:50<00:00, 59.64s/it]

25 . video_25 no. of frames= 5178.0 Output dimension= (345, 1024)


In [ ]:
# extract_features(videos_path=tvsum_data+'/video', h5output_path=hashbasedFt_path+'/TVSum.h5',method='hashbased', names=vnames)

---------------------------

##### *H5File metadata*

In [21]:
cap.release()

In [24]:
cap = cv2.VideoCapture('../data/Public datasets/ydata-tvsum50-v1_1/video/-esJrBWj2d8.mp4')
frame_count = cap.get(cv2.CAP_PROP_FRAME_COUNT)
fps = cap.get(cv2.CAP_PROP_FPS)
while cap.isOpened():
    ret, fr = cap.read()
    print(fr)
cap.release()

[[[  8  13  19]
  [  8  13  19]
  [  6  11  17]
  ...
  [  5  14  29]
  [  4  13  28]
  [  3  12  27]]

 [[  8  13  19]
  [  6  11  17]
  [  6  11  17]
  ...
  [  5  14  29]
  [  4  13  28]
  [  3  12  27]]

 [[  6  11  17]
  [  6  11  17]
  [  5  10  16]
  ...
  [  3  14  29]
  [  0  14  28]
  [  0  13  27]]

 ...

 [[ 47  89 121]
  [ 50  92 124]
  [ 53  95 127]
  ...
  [ 52  84 118]
  [ 52  84 118]
  [ 52  84 118]]

 [[ 52  89 122]
  [ 57  94 127]
  [ 58  95 128]
  ...
  [ 54  86 120]
  [ 52  84 118]
  [ 52  84 118]]

 [[ 54  91 124]
  [ 58  95 128]
  [ 58  95 128]
  ...
  [ 55  87 121]
  [ 54  86 120]
  [ 52  84 118]]]
[[[  8  13  19]
  [  8  13  19]
  [  6  11  17]
  ...
  [  5  14  29]
  [  4  13  28]
  [  3  12  27]]

 [[  8  13  19]
  [  6  11  17]
  [  6  11  17]
  ...
  [  5  14  29]
  [  4  13  28]
  [  3  12  27]]

 [[  6  11  17]
  [  6  11  17]
  [  5  10  16]
  ...
  [  3  14  29]
  [  0  14  28]
  [  0  13  27]]

 ...

 [[ 47  89 121]
  [ 50  92 124]
  [ 53  95 127]
  ..

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[[[ 35  23  35]
  [ 35  23  35]
  [ 33  21  33]
  ...
  [ 51  58  85]
  [ 49  56  83]
  [ 46  53  80]]

 [[ 25  13  25]
  [ 25  13  25]
  [ 24  12  24]
  ...
  [ 46  53  80]
  [ 46  53  80]
  [ 44  51  78]]

 [[ 22  10  22]
  [ 22  10  22]
  [ 22  10  22]
  ...
  [ 44  51  78]
  [ 44  51  78]
  [ 44  51  78]]

 ...

 [[ 73  86 114]
  [ 74  87 115]
  [ 76  89 117]
  ...
  [ 67  70  81]
  [ 71  71  83]
  [ 74  74  86]]

 [[ 72  85 113]
  [ 73  86 114]
  [ 75  88 116]
  ...
  [ 67  70  81]
  [ 71  71  83]
  [ 76  76  88]]

 [[ 72  85 113]
  [ 72  85 113]
  [ 74  87 115]
  ...
  [ 68  71  82]
  [ 73  73  85]
  [ 77  77  89]]]
[[[ 30  18  30]
  [ 30  18  30]
  [ 30  18  30]
  ...
  [ 51  58  85]
  [ 49  56  83]
  [ 49  56  83]]

 [[ 23  11  23]
  [ 23  11  23]
  [ 23  11  23]
  ...
  [ 49  56  83]
  [ 49  56  83]
  [ 49  56  83]]

 [[ 22  10  22]
  [ 22  10  22]
  [ 22  10  22]
  ...
  [ 45  52  79]
  [ 45  52  79]
  [ 45  52  79]]

 ...

 [[ 70  83 111]
  [ 72  85 113]
  [ 74  87 115]
  ..

KeyboardInterrupt: 

In [3]:
import numpy as np

In [13]:
fps=29
x = fps//2

arr = np.zeros(100)

for i in range(100):
    if i%x==0:
        arr[i]=i

In [14]:
arr

array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0., 14.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0., 28.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0., 42.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0., 56.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0., 70.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0., 84.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0., 98.,  0.])